In [1]:
from __future__ import print_function

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

import math as m
from time import time
from scipy import stats

In [2]:
import sys
print (sys.version)
if sys.version_info >= (3,4):
    print( "with enums" )
    from enum import Enum
    class CallPut(Enum):
        call = 1
        put = 2
else:
    print( "no enums" )
    class CallPut(object):
        __values__ = ['call', 'put']
        
        def __init__(self, t, s):
            self.value = t
            self.str_value = s

        
        def __eq__(self,y):
            if type(y) is not self.__class__:
                return False
            return self.value == y.value

        def __str__(self):
            return self.str_value
        
        @classmethod 
        def __enum_init__(cls):
            for i in range(len(cls.__values__)):
                setattr(cls, cls.__values__[i], CallPut(i+1, cls.__values__[i]))


    CallPut.__enum_init__()
            
t = CallPut.call
print( "Call: %s; Booleans: %r, %r " %(t, CallPut.call == t, CallPut.put == t) )
print( "Wrong type: %r" % (t == 1) )

2.7.10 (default, Dec 28 2015, 04:30:58) 
[GCC 5.2.1 20151010]
no enums
Call: call; Booleans: True, False 
Wrong type: False


In [3]:
def N(x):
    return stats.norm.cdf(x, 0.0, 1.0)

def NPrime(x):
    return stats.norm.pdf(x, 0.0, 1.0)

def bsm_d1(S, K, T, r, q, sigma):
    S = float(S)
    return (m.log(S / K) + (r - q + 0.5 * sigma ** 2) * T) / (sigma * m.sqrt(T))

def bsm_d2(S, K, T, r, q, sigma):
    S = float(S)
    return (m.log(S / K) + (r - q - 0.5 * sigma ** 2) * T) / (sigma * m.sqrt(T))

def bsm_pv(callPutType, S, K, T, r, q, sigma):
    d1 = bsm_d1(S, K, T, r, q, sigma)
    d2 = bsm_d2(S, K, T, r, q, sigma)
    if CallPut.call == callPutType:
        return S * N(d1) * m.exp(-q * T) - K * m.exp(-r * T) * N(d2)
    else:
        return K * N(-d2) * m.exp(-r * T)  - S * m.exp(-q * T) * N(-d1)

def bsm_delta(callPutType, S, K, T, r, q, sigma):
    d1 = bsm_d1(S, K, T, r, q, sigma)
    if CallPut.call == callPutType:
        return N(d1) * m.exp(-q * T)
    else:
        return -N(-d1) * m.exp(-q * T)
#S0 = 80.; K = 85.; T = 1.0; r = 0.05; q = 0.0;
#sigma = 0.2
#ref_pv = bsm_pv(CallPut.call, S=S0, K=K, T=T, r=r, q=q, sigma=sigma)
#ref_delta = bsm_delta(CallPut.call, S=S0, K=K, T=T, r=r, q=q, sigma=sigma)
#print( "ref_pv: %.6f, ref_delta: %.6f " % (ref_pv, ref_delta) )


ref_pv: 5.988244, ref_delta: 0.518694 


In [4]:
# Parameters
M = 360; I = 50000
S = 80.; K = 80.; T = 2./12; r = 0.05; q = 0.02;
delta = 0.5
sigma = 0.2

In [5]:
from scipy import optimize
import scipy

In [10]:
def mc_call_pv0(optype, cp, S0, K, T, r, q, sigma, M, I):
    # Simulating I paths with M time steps
    cp_coeff = 0;
    if (cp == CallPut.call):
        cp_coeff = 1;
    else:
        cp_coeff = -1;
    S = np.zeros((M + 1, I))
    avrS = S0
    S[0] = S0
    dt = float(T) / M
    for t in range(1, M + 1):
        z = np.random.standard_normal(I)
        mean = np.mean(z)
        std = np.std(z)
        z = (z - mean)/std
        S[t] = S[t - 1] * np.exp(((r -q) -0.5 * sigma ** 2) * dt + sigma * m.sqrt(dt) * z)
    # Calculating the Monte Carlo estimator
    if(optype == 'asian'):
        C = m.exp(-r * T)* (np.sum(np.maximum(cp_coeff*(np.apply_along_axis(np.sum,0,S)/ M - K), 0)) / I)
    else:
        C = m.exp(-r * T) * np.sum(np.maximum(cp_coeff*(S[-1] - K), 0)) / I
    return C

In [15]:
C = mc_call_pv0("asian", CallPut.call,S0, K, T, r, q, sigma, M, I)

print( "PV: %.5f" % C )

PV: 1.71485
